In [55]:
import pandas as pd
import string
import emoji
import re
import csv
from sklearn.decomposition import LatentDirichletAllocation
import random

### Step 1: Prepare the data

In [56]:
reviews = pd.read_csv('../02.Dataset/reviews.csv')

In [57]:
reviews.head(100)

ProductID  ...                                            Comment
0   192733741  ...  Nội dung hấp dẫn lôi cuốn người đọc. Bố cục rõ...
1   192733741  ...  Than moi THANH den nhan QUA va tham gia Hoi Sa...
2   192733741  ...  không có bọc kín,buồn. Góc trên bìa sách bị th...
3   192733741  ...  Giao hàng nhanh chóng, buổi tối đặt và trưa hô...
4   192733741  ...  bản này bìa nhìn đẹp hơn bản cũ, nội dung hay....
..        ...  ...                                                ...
95  173364636  ...  Sách rất hay, dù mình đã xem phim nhưng quả th...
96  173364636  ...  Bị df bìa ngoài, đóng gói quen thuộc của tiki....
97  173364636  ...  Để trong giỏ hàng lâu rồi, giờ có hội sách đượ...
98  173364636  ...  1. Hình thức: các bạn cx thấy r ha, bìa siêu x...
99  173364636  ...  Sách đẹp ổn tuy nhiên trong quá trình vận chuy...

[100 rows x 4 columns]

In [58]:
reviews.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 37765 entries, 0 to 37764
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   ProductID   37765 non-null  int64 
 1   CustomerID  37765 non-null  int64 
 2   Rating      37765 non-null  int64 
 3   Comment     37765 non-null  object
dtypes: int64(3), object(1)
memory usage: 1.2+ MB


### Step 2: Preprocessing

In [59]:
# Clean icons
def clean_icons(text):
    text = emoji.replace_emoji(text, replace="")
    text = re.sub(r"[:;][-~]?[)D(/\\|pP]", "", text)
    text = text.replace("_x000D_", " ")
    return text

def lower(text):
    return text.lower().strip()

def remove_links(text):
    return re.sub(r"http\S+|www\S+|https\S+", "", text, flags=re.MULTILINE)

# Convert comment to a full sentence
def convert_teencode_to_vietnamese(sentence, dictionary):
    words = sentence.split()
    converted_words = []
    for word in words:
        if word in dictionary:
            converted_words.append(dictionary[word])
            continue

        punctuation = ""
        temp_word = word
        while temp_word and temp_word[-1] in string.punctuation:
            punctuation = temp_word[-1] + punctuation
            temp_word = temp_word[:-1]
        if temp_word in dictionary:
            converted_words.append(dictionary[temp_word] + punctuation)
            continue

        leading_punctuation = ""
        temp_word = word
        while temp_word and temp_word[0] in string.punctuation:
            leading_punctuation += temp_word[0]
            temp_word = temp_word[1:]
        if temp_word in dictionary:
            converted_words.append(leading_punctuation + dictionary[temp_word])
            continue

        converted_words.append(word)

    return " ".join(converted_words)

# Remove stopwords
vietnamese_stopwords = [
    "à", "á", "ạ", "ả", "ã", "â", "ầ", "ấ", "ậ", "ẩ", "ẫ", "ă", "ằ", "ắ", "ặ", "ẳ", "ẵ",
    "è", "é", "ẹ", "ẻ", "ẽ", "ê", "ề", "ế", "ệ", "ể", "ễ",
    "ì", "í", "ị", "ỉ", "ĩ",
    "ò", "ó", "ọ", "ỏ", "õ", "ô", "ồ", "ố", "ộ", "ổ", "ỗ", "ơ", "ờ", "ớ", "ợ", "ở", "ỡ",
    "ù", "ú", "ụ", "ủ", "ũ", "ư", "ừ", "ứ", "ự", "ử", "ữ",
    "ỳ", "ý", "ỵ", "ỷ", "ỹ",
    "đ",
    "và", "là", "của", "có", "cho", "với", "một", "những", "các", "này", "trong", "khi", "đó",
    "ở", "ra", "lên", "xuống", "về", "từ", "đến", "bằng", "để", "do", "nên", "thì", "mà",
    "vẫn", "đã", "đang", "sẽ", "cũng", "rất", "nhiều", "ít", "hơn", "nữa",
    "tôi", "bạn", "anh", "chị", "họ", "chúng", "chúng_tôi", "chúng_ta", "các_bạn", "mọi_người",
    "ai", "gì", "cái", "nào", "vậy", "như", "thế", "nào", "đây", "đấy", "ấy", "kìa", "kia",
    "vì", "nhưng", "hoặc", "và", "nếu", "thì", "mà", "lại", "vừa", "thế_là",
    "ngay", "luôn", "liền", "đúng", "sai",
    "cùng", "theo", "trước", "sau", "khi_nào", "bao_giờ", "bây_giờ", "từ_đâu", "ở_đâu", "thế_nào",
    "cần", "có_thể", "được", "bị", "phải", "nên", "cần_phải",
    "hết", "rồi", "luôn", "lúc", "ngày", "tháng", "năm",
    "này", "kia", "ấy", "đó", "vậy", "như_vậy", "vậy_nên"
]

def remove_stopwords(text):
    return " ".join([word for word in text.split() if word not in vietnamese_stopwords])

In [60]:
from pyvi import ViTokenizer

def word_segmentation(text):
  if pd.isna(text):
      return ""
  return ViTokenizer.tokenize(text)

In [61]:
dictionary = {}
with open(
    "../02.Dataset/teencode.csv",
    mode="r",
    encoding="utf-8",
) as file:
    reader = csv.DictReader(file)
    for row in reader:
        dictionary[row["Teencode"]] = row["Meaning"]

reviews["Comment"] = reviews["Comment"].apply(clean_icons)
reviews["Comment"] = reviews["Comment"].apply(lower)
reviews["Comment"] = reviews["Comment"].apply(remove_links)
reviews["Comment"] = reviews["Comment"].apply(remove_stopwords)
reviews["Comment"] = reviews["Comment"].apply(
    lambda x: convert_teencode_to_vietnamese(x, dictionary)
)

# Word segmentation
reviews["Comment"] = reviews["Comment"].apply(word_segmentation)

reviews.dropna(subset=["Comment"], inplace=True)
reviews.reset_index(drop=True, inplace=True)

In [62]:
reviews.head()

ProductID  ...                                            Comment
0  192733741  ...  nội_dung hấp_dẫn lôi_cuốn người đọc . bố_cục r...
1  192733741  ...  than moi thanh den nhan qua va tham_gia hoi sa...
2  192733741  ...  không bọc kín , buồn . góc trên bìa sách thiếu...
3  192733741  ...  giao hàng nhanh_chóng , buổi tối đặt trưa hôm ...
4  192733741  ...  bản bìa nhìn đẹp bản cũ , nội_dung hay . rcm m...

[5 rows x 4 columns]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer

tfidf = TfidfVectorizer(max_df=0.95, min_df=2)

In [64]:
dtm = tfidf.fit_transform(reviews["Comment"])

In [65]:
dtm

<Compressed Sparse Row sparse matrix of dtype 'int64'
	with 385554 stored elements and shape (37765, 7281)>

## LatentDirichletAllocation

In [66]:
LDA = LatentDirichletAllocation(n_components=3, random_state=42)

In [67]:
LDA.fit(dtm)

LatentDirichletAllocation(n_components=3, random_state=42)

### Showing Stored Words

In [68]:
len(tfidf.get_feature_names_out())

7281

In [69]:
for i in range(10):
    random_word_id = random.randint(0, 2662)
    print(tfidf.get_feature_names_out()[random_word_id])

cứng
cấn
bảy
giad
358
day
bàn_giao
hỏng_hóc
hòa
bìa_vầy


### Showing Top Words Per Topic

In [70]:
len(LDA.components_)

3

In [71]:
LDA.components_

array([[8.32367045, 3.20916971, 7.12457977, ..., 0.33351449, 0.33352882,
        0.33351449],
       [0.33976065, 0.35438518, 0.34657374, ..., 4.33302269, 6.33299464,
        4.33302269],
       [0.3365689 , 4.43644512, 2.52884648, ..., 0.33346282, 0.33347654,
        0.33346282]], shape=(3, 7281))

In [72]:
single_topic = LDA.components_[0]

In [73]:
# Returns the indices that would sort this array.
single_topic.argsort()

array([5803,  684, 4640, ..., 3806, 2242, 1778], shape=(7281,))

In [74]:
# Word least representative of this topic
single_topic[1131]

np.float64(21.542583586414803)

In [75]:
# Word most representative of this topic
single_topic[770]

np.float64(9.633595750187528)

In [76]:
# Top 10 words for this topic:
single_topic.argsort()[-10:]

array([2049, 3321, 6149, 5483, 6934, 7045, 4874, 3806, 2242, 1778])

In [77]:
top_word_indices = single_topic.argsort()[-10:]

In [78]:
for index in top_word_indices:
    print(tfidf.get_feature_names_out()[index])

hay
mua
tốt
tiki
đóng_gói
đẹp
sách
nhanh
hàng
giao


In [79]:
for index, topic in enumerate(LDA.components_):
    print(f"THE TOP 15 WORDS FOR TOPIC #{index}")
    print([tfidf.get_feature_names_out()[i] for i in topic.argsort()[-15:]])
    print("\n")

THE TOP 15 WORDS FOR TOPIC #0
['mới', 'sản_phẩm', 'đọc', 'mình', 'cẩn_thận', 'hay', 'mua', 'tốt', 'tiki', 'đóng_gói', 'đẹp', 'sách', 'nhanh', 'hàng', 'giao']


THE TOP 15 WORDS FOR TOPIC #1
['hàng', 'tiki', 'móp', 'đóng_gói', 'giấy', 'nội_dung', 'mình', 'hay', 'hơi', 'bọc', 'bìa', 'ổn', 'đẹp', 'không', 'sách']


THE TOP 15 WORDS FOR TOPIC #2
['đáng', 'cách', 'dễ', 'tác_giả', 'thấy', 'quyển', 'hiểu', 'nội_dung', 'không', 'người', 'cuốn', 'hay', 'mình', 'đọc', 'sách']




### Attaching Discovered Topic Labels to Original Comment

In [80]:
topic_results = LDA.transform(dtm)

In [81]:
topic_results.shape

(37765, 3)

In [82]:
topic_results[0]

array([0.03167852, 0.37280104, 0.59552044])

In [83]:
topic_results[0].round(2)

array([0.03, 0.37, 0.6 ])

In [84]:
topic_results[0].argmax()

np.int64(2)

In [85]:
reviews.head()

ProductID  ...                                            Comment
0  192733741  ...  nội_dung hấp_dẫn lôi_cuốn người đọc . bố_cục r...
1  192733741  ...  than moi thanh den nhan qua va tham_gia hoi sa...
2  192733741  ...  không bọc kín , buồn . góc trên bìa sách thiếu...
3  192733741  ...  giao hàng nhanh_chóng , buổi tối đặt trưa hôm ...
4  192733741  ...  bản bìa nhìn đẹp bản cũ , nội_dung hay . rcm m...

[5 rows x 4 columns]

In [86]:
topic_results.argmax(axis=1)

array([2, 0, 1, ..., 2, 0, 1], shape=(37765,))

In [87]:
reviews["Topic"] = topic_results.argmax(axis=1)

In [88]:
reviews.head(10)

ProductID  ...  Topic
0  192733741  ...      2
1  192733741  ...      0
2  192733741  ...      1
3  192733741  ...      0
4  192733741  ...      1
5  192733741  ...      0
6  192733741  ...      1
7  192733741  ...      0
8  192733741  ...      0
9  192733741  ...      1

[10 rows x 5 columns]

In [89]:
reviews['Topic'].value_counts()

Topic
0    14297
1    12586
2    10882
Name: count, dtype: int64

In [90]:
for id,pro_id,cus_id,raing,comment,topic in reviews[reviews['Topic'] == 0].itertuples():
    print(f"ID: {id}, Product ID: {pro_id}, Customer ID: {cus_id}, Topic: {topic}")
    print(comment)
    print("\n")

ID: 1, Product ID: 192733741, Customer ID: 14177076, Topic: 0
than moi thanh den nhan qua va tham_gia hoi sach xa kho - ban can 49k / 1kg . luc 8h - 22h tu 17 / 7 den 21 / 7 tai nha van hoa , so 3 le duan , tp buon ma thuot .


ID: 3, Product ID: 192733741, Customer ID: 22009546, Topic: 0
giao hàng nhanh_chóng , buổi tối đặt trưa hôm có . sách đóng_gói cẩn_thận , gọn_gàng .


ID: 5, Product ID: 192733741, Customer ID: 26572209, Topic: 0
mười điểm khâu đóng_gói chưa chắc_chắn lắm lần sách mình nguyên_vẹn


ID: 7, Product ID: 192733741, Customer ID: 10607102, Topic: 0
thiết_kế bìa mới đẹp , mình nghe nói nội_dung hay mua tặng làm_quà ^ ^


ID: 8, Product ID: 192733741, Customer ID: 21647349, Topic: 0
bìa siêu đẹp , tiki giao hàng nhanh ổn rùi , mong cải_tiến khâu đóng_gói thuu


ID: 10, Product ID: 192733741, Customer ID: 19400620, Topic: 0
lần bìa đẹp zã man . sách hay . mọi người mua nhaaa


ID: 11, Product ID: 192733741, Customer ID: 23130630, Topic: 0
thích quyển giảm_giá mua


ID: 1

In [91]:
for id,pro_id,cus_id,raing,comment,topic in reviews[reviews['Topic'] == 1].itertuples():
    print(f"ID: {id}, Product ID: {pro_id}, Customer ID: {cus_id}, Topic: {topic}")
    print(comment)
    print("\n")

ID: 2, Product ID: 192733741, Customer ID: 27497576, Topic: 1
không bọc kín , buồn . góc trên bìa sách thiếu nhìn xấu quá . chưa đọc biết sơ điện_ảnh mua xem thử .


ID: 4, Product ID: 192733741, Customer ID: 7426060, Topic: 1
bản bìa nhìn đẹp bản cũ , nội_dung hay . rcm mua nha mọi người ! !


ID: 6, Product ID: 192733741, Customer ID: 20882294, Topic: 1
tái_bản bìa mới mua , chứ bìa cũ nhìn chán lắm , sách đẹp !


ID: 9, Product ID: 192733741, Customer ID: 7525460, Topic: 1
chất_lượng giấy mực in tốt , thiết_kế bìa đẹp , đáng lưu_trữ


ID: 19, Product ID: 187827390, Customer ID: 12864847, Topic: 1
vận chuyện nhanh , mọi lần ổn lần vận_chuyển ẩu quá , nhìn hộp nó móp nghi nghi rồi , may sách chỉ hỏng


ID: 22, Product ID: 187827390, Customer ID: 6117686, Topic: 1
bìa màu đẹp , bao sách kĩ_càng , bookmark xinh_xắn . sách hay tuyệt_vời .


ID: 24, Product ID: 187827390, Customer ID: 28073417, Topic: 1
hay , nghĩa , đóng_gói hàng không quá miếng chống sốc làm bìa cong


ID: 28, Product I

In [92]:
for id,pro_id,cus_id,raing,comment,topic in reviews[reviews['Topic'] == 2].itertuples():
    print(f"ID: {id}, Product ID: {pro_id}, Customer ID: {cus_id}, Topic: {topic}")
    print(comment)
    print("\n")

ID: 0, Product ID: 192733741, Customer ID: 18387707, Topic: 2
nội_dung hấp_dẫn lôi_cuốn người đọc . bố_cục rõ_ràng . in_ấn sắc nét .


ID: 13, Product ID: 192733741, Customer ID: 7297183, Topic: 2
nội_dung cực_kỳ lôi_cuốn !


ID: 14, Product ID: 192733741, Customer ID: 21725158, Topic: 2
hay


ID: 16, Product ID: 187827390, Customer ID: 27737542, Topic: 2
mình thật_sự không_thể giữ giọt lệ không rơi đọc cuốn tiểu_thuyết này . khóc mỉm cười mọi thứ qua , khóc tuyệt_vọng lần ập tới , an lòng nó qua đi . đọc từng câu chữ khiến mình lạnh cả sống_lưng , căng_thẳng dồn_dập , cảm_giác thể mình nhân_vật chính , nỗi sợ sắp chứng_kiến điều_kinh_khủng sắp xảy ý . * * * không hẳn spoil , thể khiến hình_dung phần câu_chuyện đọc tới chưa đọc tới . mình vô thương_xót người con_gái ấy , yêu mức phản_bội yêu người ấy , tình_yêu con_gái lớn tới mức cả bầu_trời chắc không chứa nổi . tiểu_thuyết lấy đi giọt nước_mắt , nỗi buồn_phiền nhớ quá_khứ nhân_vật , thấy hiện_thực tàn_khốc , sự giả_dối , giả_tạo sự 

## Non Negative Matrix Factorization

In [93]:
from sklearn.decomposition import NMF

In [94]:
nmf_model = NMF(n_components=3, random_state=42)

In [95]:
nmf_model.fit(dtm)

NMF(n_components=3, random_state=42)

In [96]:
single_topic = nmf_model.components_[0]

In [97]:
# Returns the indices that would sort this array.
single_topic.argsort()

array([7246, 3499, 3513, ..., 7103, 2632, 3387], shape=(7281,))

In [98]:
# Word least representative of this topic
single_topic[7246]

np.float64(0.0)

In [99]:
# Word most representative of this topic
single_topic[3387]

np.float64(10.986779984781979)

In [100]:
# Top 10 words for this topic:
single_topic.argsort()[-10:]

array([1221, 2966, 4094, 1003, 5362, 1160, 3715, 7103, 2632, 3387])

In [101]:
top_word_indices = single_topic.argsort()[-10:]

In [103]:
for index in top_word_indices:
    print(tfidf.get_feature_names_out()[index])

còn
làm
nó
chỉ
thấy
cuốn
người
đọc
không
mình


In [105]:
for index, topic in enumerate(nmf_model.components_):
    print(f"THE TOP 15 WORDS FOR TOPIC #{index}")
    print([tfidf.get_feature_names_out()[i] for i in topic.argsort()[-15:]])
    print("\n")

THE TOP 15 WORDS FOR TOPIC #0
['cách', 'mọi', 'tác_giả', 'thể', 'sự', 'còn', 'làm', 'nó', 'chỉ', 'thấy', 'cuốn', 'người', 'đọc', 'không', 'mình']


THE TOP 15 WORDS FOR TOPIC #1
['khá', 'giấy', 'hơi', 'mới', 'tiki', 'bọc', 'bìa', 'cuốn', 'mua', 'đọc', 'nội_dung', 'không', 'đẹp', 'hay', 'sách']


THE TOP 15 WORDS FOR TOPIC #2
['chưa', 'gói', 'siêu', 'sản_phẩm', 'đặt', 'chất_lượng', 'tốt', 'cẩn_thận', 'không', 'đẹp', 'đóng_gói', 'tiki', 'nhanh', 'hàng', 'giao']




In [106]:
topic_results.argmax(axis=1)

array([2, 0, 1, ..., 2, 0, 1], shape=(37765,))

In [108]:
reviews["Topic"] = topic_results.argmax(axis=1)

In [110]:
reviews.head(10)

ProductID  ...  Topic
0  192733741  ...      2
1  192733741  ...      0
2  192733741  ...      1
3  192733741  ...      0
4  192733741  ...      1
5  192733741  ...      0
6  192733741  ...      1
7  192733741  ...      0
8  192733741  ...      0
9  192733741  ...      1

[10 rows x 5 columns]